In [1]:
"""Model performance on different complexity problems."""
import seaborn as sns
from matplotlib import rcParams
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

from visualize_utils import *

################################################################################################
#### Plot setting                                                                           ####
################################################################################################

rcParams['figure.dpi'] = 500
rcParams['savefig.dpi'] = 500
rcParams['figure.figsize'] = 30, 24
rcParams['font.family'] = 'Arial'
rcParams['font.size'] = 18
rcParams['axes.labelsize'] = 18
rcParams['axes.titlesize'] = 18
rcParams['xtick.labelsize'] = 14
rcParams['ytick.labelsize'] = 18
rcParams['legend.fontsize'] = 18
rcParams['figure.titlesize'] = 18
rcParams['markers.fillstyle'] = 'none'

################################################################################################
#### Load and aggregate the results                                                         ####
################################################################################################
PRE_DIR = '../'
RESULT_DIR = PRE_DIR + 'rq3'

In [2]:
difficulty_sets = []
model_names = []
problem_names = []
finetune_times = []
avg_accuracies = []
raw_accuracies = []
raw_failures = []

for dir in os.listdir(RESULT_DIR):
    if not os.path.isdir(os.path.join(RESULT_DIR, dir)):
        continue
    mode, difficulty_set = dir.split('_')
    current_dir = os.path.join(RESULT_DIR, dir)
    for file in os.listdir(current_dir):
        if file.endswith('.json'):
            file_infos = file.split('.')[0].split('_')
            model_name = file_infos[0]
            if file_infos[-1].startswith("benchmark"):
                finetune_time = file_infos[-1][-1]
                problem_name = "_".join(file_infos[1:-1])
            else:
                finetune_time = '0'
                problem_name = "_".join(file_infos[1:])
            performance = calculate_accuracy(fetch_one_file(file, current_dir, model_name, problem_name))
            raw_accuracy = performance['accuracy']
            num_levels = len(raw_accuracy)
            avg_accuracy = np.average(raw_accuracy, weights=list(range(1, 11)))
            avg_failure = np.mean(performance['failed'])

            difficulty_sets.append(difficulty_set)
            model_names.append(model_name)
            problem_names.append(problem_name)
            finetune_times.append(finetune_time)
            avg_accuracies.append(avg_accuracy)
            raw_accuracies.append(np.mean(raw_accuracy))
            raw_failures.append(avg_failure)

mistral on tsp_d_Results has 94 failed results
phi-2 on tspResults has 16 failed results
mistral on gcp_d_Results has 9 failed results
qwen on bspResults has 2 failed results
mistral on mspResults has 95 failed results
qwen on gcp_d_Results has 100 failed results
gpt-4-1106-preview on tspResults has 1 failed results
mistral on tsp_d_Results has 4 failed results
phi-2 on tsp_d_Results has 100 failed results
qwen on sppResults has 12 failed results
phi-2 on bspResults has 1 failed results
phi-2 on bspResults has 15 failed results
mistral on edpResults has 4 failed results
phi-2 on gcpResults has 74 failed results
mistral on gcp_d_Results has 36 failed results
qwen on gcpResults has 93 failed results
phi-2 on sppResults has 4 failed results
qwen on tsp_d_Results has 100 failed results
mistral on sppResults has 71 failed results
phi-2 on bspResults_BSP_0 has 67 failed results
mistral on tspResults has 98 failed results
phi-2 on gcp_d_Results has 100 failed results
qwen on mspResults has 10

In [3]:
new_df = pd.DataFrame({
    'difficulty_set': difficulty_sets,
    'model_name': model_names,
    'problem_name': problem_names,
    'finetune_time': finetune_times,
    'avg_accuracy': avg_accuracies,
    'raw_accuracy': raw_accuracies,
    'raw_failure': raw_failures
})

In [4]:
new_df.problem_name.unique()

array(['tsp_d_Results', 'edpResults', 'kspResults', 'tspResults',
       'gcp_d_Results', 'sppResults', 'bspResults', 'mspResults',
       'gcpResults', 'bspResults_BSP_0', 'mfpResults'], dtype=object)

In [5]:
new_df

difficulty_set model_name   problem_name finetune_time  avg_accuracy  \
0             easy    mistral  tsp_d_Results             1      0.000000   
1             easy    mistral     edpResults             5      0.390909   
2             easy    mistral     kspResults             3      0.000000   
3             easy      phi-2     tspResults             0      0.010909   
4             easy    mistral  gcp_d_Results             0      0.580000   
..             ...        ...            ...           ...           ...   
288         medium    mistral     bspResults             3      0.589091   
289         medium    mistral     tspResults             4      0.000000   
290         medium       qwen     sppResults             1      0.041818   
291         medium      phi-2  gcp_d_Results             4      0.000000   
292         medium    mistral     gcpResults             5      0.000000   

     raw_accuracy  raw_failure  
0            0.00         0.94  
1            0.48         0.00  
2            0.00         0.00  
3            0.06         0.16  
4            0.58         0.09  
..            ...          ...  
288          0.67         0.32  
289          0.00         0.96  
290          0.08         0.00  
291          0.00         0.86  
292          0.00         0.69  

[293 rows x 7 columns]

In [6]:
rename_problem_mapper = {
    'sppResults': 'SPP', 'mfpResults': 'MFP', 'bspResults': 'SAS', 'edpResults': 'EDP',
    'tsp_d_Results': 'TSP_D', 'gcp_d_Results': 'GCP_D', 'kspResults': 'KSP',
    'tspResults': 'TSP', 'gcpResults': 'GCP', 'mspResults': 'MSP'}

In [7]:
new_df['model_name'] = new_df['model_name'].map(lambda x: model_mapper[x] if x in model_mapper else x)
new_df['problem_name'] = new_df['problem_name'].map(rename_problem_mapper)

In [8]:
new_df

difficulty_set  model_name problem_name finetune_time  avg_accuracy  \
0             easy  Mistral-7b        TSP_D             1      0.000000   
1             easy  Mistral-7b          EDP             5      0.390909   
2             easy  Mistral-7b          KSP             3      0.000000   
3             easy       Phi-2          TSP             0      0.010909   
4             easy  Mistral-7b        GCP_D             0      0.580000   
..             ...         ...          ...           ...           ...   
288         medium  Mistral-7b          SAS             3      0.589091   
289         medium  Mistral-7b          TSP             4      0.000000   
290         medium    Qwen-14b          SPP             1      0.041818   
291         medium       Phi-2        GCP_D             4      0.000000   
292         medium  Mistral-7b          GCP             5      0.000000   

     raw_accuracy  raw_failure  
0            0.00         0.94  
1            0.48         0.00  
2            0.00         0.00  
3            0.06         0.16  
4            0.58         0.09  
..            ...          ...  
288          0.67         0.32  
289          0.00         0.96  
290          0.08         0.00  
291          0.00         0.86  
292          0.00         0.69  

[293 rows x 7 columns]

In [9]:
new_df.finetune_time.unique()

array(['1', '5', '3', '0', '2', '4'], dtype=object)

In [10]:
np.min(new_df['avg_accuracy'] - new_df['raw_accuracy'])

-0.18

In [11]:
sum(new_df['avg_accuracy'] == 0)

167

In [12]:
sum(new_df['raw_accuracy'] == 0)

167

In [13]:
problem = "SAS"
difficulty = "medium"
problem_df = new_df[new_df['problem_name'] == problem]
difficulty_df = problem_df[problem_df['difficulty_set'] == difficulty]
print(problem, difficulty_df.model_name.unique())
difficulty_df_pivot = difficulty_df.pivot_table(index='finetune_time', columns='model_name', values='avg_accuracy', aggfunc='mean')
difficulty_df_pivot

SAS ['Qwen-14b' 'Phi-2' 'GPT 4 Turbo' 'Mistral-7b']


model_name     GPT 4 Turbo  Mistral-7b     Phi-2  Qwen-14b
finetune_time                                             
0                 0.983636    0.029091  0.072727  0.463636
1                      NaN    0.618182  0.310909  0.705455
2                      NaN    0.680000  0.463636  0.745455
3                      NaN    0.589091  0.530909  0.849091
4                      NaN    0.705455  0.669091  0.838182
5                      NaN    0.638182  0.609091  0.830909

In [14]:
from itertools import product

problem_diff = list(product(['SAS', 'EDP', 'SPP', 'GCP_D', 'TSP_D', 'KSP', 'GCP', 'TSP'], ['easy', 'medium']))

fig, _ = plt.subplots(4, 4)
for i, (problem, difficulty) in enumerate(problem_diff):
    try:
        problem_df = new_df[new_df['problem_name'] == problem]
        difficulty_df = problem_df[problem_df['difficulty_set'] == difficulty]
        print(problem, difficulty_df.model_name.unique())
        difficulty_df_pivot = difficulty_df.pivot_table(index='finetune_time', columns='model_name', values='avg_accuracy', aggfunc='mean')
        mean_df = difficulty_df_pivot.mean(axis=0).to_frame().T
        # set latex bold of 'Mean'
        mean_df.index = ['Mean']
        df = pd.concat([mean_df, difficulty_df_pivot])[['GPT 4 Turbo', 'Qwen-14b', 'Mistral-7b', 'Phi-2']]
        plt.subplot(4, 4, i+1)
        sns.heatmap(df, annot=True, cmap='Blues', vmin=0.0, vmax=1.0, fmt='.3f', cbar=False)
        # add a horizontal line
        plt.axhline(y=1, color='black', linewidth=3)
        plt.xlabel(None)
        plt.ylabel('Finetune Times')
        plt.title(f'{chr(97 + i)}. {difficulty.title()} {problem} Problems',  loc='left')
    except:
        pass
fig.subplots_adjust(right=0.95)
cbar_ax = fig.add_axes([0.97, 0.5, 0.02, 0.4])
fig.colorbar(ax=fig.axes, cax=cbar_ax,
                mappable=fig.axes[0].collections[0], orientation='vertical')
# plt.savefig(f'figures/ablation/{problem}_accuracy.png', bbox_inches='tight')
plt.savefig(PRE_DIR + f'figures/rq3/rq3_weighted_accuracy.png', bbox_inches='tight')

SAS ['Qwen-14b' 'Phi-2' 'GPT 4 Turbo' 'Mistral-7b']
SAS ['Qwen-14b' 'Phi-2' 'GPT 4 Turbo' 'Mistral-7b']
EDP ['Mistral-7b' 'Qwen-14b' 'Phi-2' 'GPT 4 Turbo']
EDP ['Mistral-7b' 'Qwen-14b' 'Phi-2' 'GPT 4 Turbo']
SPP ['Qwen-14b' 'Mistral-7b' 'Phi-2' 'GPT 4 Turbo']
SPP ['Qwen-14b' 'Mistral-7b' 'Phi-2' 'GPT 4 Turbo']
GCP_D ['Mistral-7b' 'Qwen-14b' 'GPT 4 Turbo' 'Phi-2']
GCP_D ['Mistral-7b' 'Qwen-14b' 'GPT 4 Turbo' 'Phi-2']
TSP_D ['Mistral-7b' 'Phi-2' 'GPT 4 Turbo' 'Qwen-14b']
TSP_D ['Mistral-7b' 'Phi-2' 'GPT 4 Turbo' 'Qwen-14b']
KSP ['Mistral-7b' 'Qwen-14b' 'Phi-2' 'GPT 4 Turbo']
KSP ['Mistral-7b' 'Qwen-14b' 'Phi-2' 'GPT 4 Turbo']
GCP ['Phi-2' 'Qwen-14b' 'GPT 4 Turbo' 'Mistral-7b']
GCP ['Phi-2' 'Qwen-14b' 'GPT 4 Turbo' 'Mistral-7b']
TSP ['Phi-2' 'GPT 4 Turbo' 'Mistral-7b' 'Qwen-14b']
TSP ['Phi-2' 'GPT 4 Turbo' 'Mistral-7b' 'Qwen-14b']
